In [2]:
import os, glob, platform, datetime
from collections import OrderedDict

import torch
import torch.nn as nn
import torch.utils.data as data_utils
import torch.nn.parallel
import torch.backends.cudnn as cudnn
import torch.optim as optim
from torch.autograd import Variable

import torchvision.datasets as datasets
import torchvision.models as models
import torchvision.transforms as transforms

import cv2
from PIL import Image
from tensorboardX import SummaryWriter

import numpy as np
from numpy.linalg import inv as denseinv
from scipy import sparse
from scipy.sparse import lil_matrix, csr_matrix
from scipy.sparse.linalg import spsolve
from scipy.sparse.linalg import inv as spinv
import scipy.misc

# Configurations

In [3]:
class Args(object):
    pass
args = Args()
args.test_scene = 'alley_1'
args.arch = "densenet121"
args.epoches = 500
args.epoches_unary_threshold = 0
args.image_h = 256
args.image_w = 256
args.img_extentions = ["png"]
args.training_thresholds = [250,200,150,50,0,300]
args.base_lr = 1
args.lr = args.base_lr
args.snapshot_interval = 5000
args.debug = True
args.gpu_num = 1
args.display_interval = 50
args.display_curindex = 0

system_ = platform.system()
system_dist, system_version, _ = platform.dist()
if system_ == "Darwin": 
    args.train_dir = '/Volumes/Transcend/dataset/sintel2'
    args.pretrained = False
elif platform.dist() ==  ('debian', 'jessie/sid', ''):
    args.train_dir = '/home/albertxavier/dataset/sintel2'
    args.pretrained = True
elif platform.dist() == ('debian', 'stretch/sid', ''):
    args.train_dir = '/home/cad/lwp/workspace/dataset/sintel2'
    args.pretrained = True

if platform.system() == 'Linux': use_gpu = True
else: use_gpu = False

if use_gpu:
    torch.cuda.set_device(args.gpu_num)
    

print(platform.dist())

('debian', 'stretch/sid', '')


# Little Test

In [4]:
# class Netxxx(nn.Module):
#     def build_blocks(self, num_block, num_init_features):
#         bn_size = 4
#         growth_rate = 32
#         drop_rate = 0
#         num_features = num_init_features
#         features = nn.Sequential()
#         for i, num_layers in enumerate(num_block):
#             block = _DenseBlock(num_layers=num_layers, num_input_features=num_features,
#                                 bn_size=bn_size, growth_rate=growth_rate, drop_rate=drop_rate)
#             features.add_module('denseblock%d' % (i + 1), block)
#             num_features = num_features + num_layers * growth_rate
            
#             trans = _MyTransition(num_input_features=num_features, num_output_features=num_features // 2)
#             features.add_module('transition%d' % (i + 1), trans)
#             num_features = num_features // 2
#         print(num_features)
#         return features

#     def __init__(self):
#         super(Netxxx, self).__init__()
#         self.bn = nn.Conv2d(kernel_size=3, in_channels=1, out_channels=1, padding=1)
# #         self.bn = nn.BatchNorm2d(1)
# #         self.fns = nn.Sequential(self.build_blocks([3,3],1),self.build_blocks([3,3],88))
# #         self.fns.add_module(self.build_blocks([3,3],64))
# #         self.fns.add_module(self.build_blocks([3,3],96))
#     def forward(self,x):
#         x = self.bn(x)
# #         x = self.fns(x)
#         return x
    
# netxxx = Netxxx()
# netxxx.cuda()

# cre = nn.MSELoss().cuda()

# optimizer = optim.SGD(net.parameters(), lr=1, momentum=0)


# x = torch.randn(1,1,3,3)
# g = torch.randn(1,1,3,3)
# x = Variable(x.cuda())
# g = Variable(g.cuda())
# y = netxxx(x)
# optimizer.zero_grad()
# loss = cre(y,g)
# loss.backward()
# print(netxxx.bn.weight.grad)

# optimizer.zero_grad()
# y = netxxx(x)
# optimizer.zero_grad()
# loss = cre(y,g)
# loss.backward()
# print(netxxx.bn.weight.grad)

# optimizer.zero_grad()
# y = netxxx(x)
# optimizer.zero_grad()
# loss = cre(y,g)
# loss.backward()
# print(netxxx.bn.weight.grad)

# optimizer.zero_grad()
# y = netxxx(x)
# optimizer.zero_grad()
# loss = cre(y,g)
# loss.backward()
# print(netxxx.bn.weight.grad)

# My DataLoader

In [5]:
def default_loader(path):
    return Image.open(path).convert('RGB')

def make_dataset(dir, phase):
    images_paths = glob.glob(os.path.join(dir, 'clean', '*', '*.png'))
    albedo_paths = images_paths[:]
    shading_paths = images_paths[:]
    pathes = []
    for img_path in images_paths:
        sp = img_path.split('/'); 
        if phase == 'train':
            if sp[-2] == args.test_scene: continue
        else:
            if sp[-2] != args.test_scene: continue
            
        sp[-3] = 'albedo'; 
        sp = ['/'] + sp; 
        albedo_path = os.path.join(*sp)
        
        sp = img_path.split('/'); 
        sp[-3] = 'shading'; 
        sp[-1] = sp[-1].replace('frame', 'out')
        sp = ['/'] + sp; 
        shading_path = os.path.join(*sp)
        
        pathes.append((img_path, albedo_path, shading_path))
    return pathes

class MyImageFolder(data_utils.Dataset):
    def __init__(self, root, phase='train', transform=None, target_transform=None,
                loader=default_loader):
        imgs = make_dataset(root, phase)
        if len(imgs) == 0:
            raise(RuntimeError("Found 0 images in subfolders of: " + root + "\n"
                               "Supported image extensions are: " + ",".join(args.img_extentions)))

        self.root = root
        self.imgs = imgs
        self.transform = transform
        self.target_transform = target_transform
        self.loader = loader
        
    def __getitem__(self, index):
        img_path, albedo_path, shading_path = self.imgs[index]
        
        img = self.loader(img_path)
        albedo = self.loader(albedo_path)
        shading = self.loader(shading_path)
        
        if self.transform is not None: img = self.transform(img)
        if self.transform is not None: albedo = self.transform(albedo)
        if self.transform is not None: shading = self.transform(shading)
        
        scene = img_path.split('/')[-2]
        return img, albedo, shading, scene, img_path
    
    def __len__(self):
        return len(self.imgs)
    
train_dataset = MyImageFolder(args.train_dir, 'train', 
                       transforms.Compose(
        [transforms.RandomCrop((args.image_h, args.image_w)),
         transforms.ToTensor()]
    ))
test_dataset = MyImageFolder(args.train_dir, 'test', 
                       transforms.Compose(
        [transforms.CenterCrop((args.image_h, args.image_w)),
         transforms.ToTensor()]
    ))

train_loader = data_utils.DataLoader(train_dataset,1,True,num_workers=1)
test_loader = data_utils.DataLoader(test_dataset,1,False,num_workers=1)

# Load Pretrained Model

[Defination](https://github.com/pytorch/vision/blob/master/torchvision/models/densenet.py)
* DenseNet-121: num_init_features=64, growth_rate=32, block_config=(6, 12, 24, 16)
    * First Convolution: 32M -> 16M -> 8M
    * every transition: 8M -> 4M -> 2M (downsample 1/2, except the last block)

In [6]:
densenet = models.__dict__[args.arch](pretrained=args.pretrained)

# for param in densenet.parameters():
#     param.requires_grad = False

if use_gpu:
    densenet.cuda()


In [7]:
# for k,v in enumerate(densenet.parameters()):
#     print (k,v)

In [8]:
class PreTrainedModel(nn.Module):
    def __init__(self, pretrained):
        super(PreTrainedModel, self).__init__()
        common_features_net = nn.Sequential(*list(pretrained.children())[0:1])
        self.net_16M = nn.Sequential(OrderedDict([
            ('conv0', common_features_net[0].conv0),
            ('norm0', common_features_net[0].norm0),
            ('relu0', common_features_net[0].relu0)
        ]))
        self.net_8M = nn.Sequential(OrderedDict([
            ('pool0', common_features_net[0].pool0)
        ]))
        self.net_4M = nn.Sequential(OrderedDict([
            ('denseblock1', common_features_net[0].denseblock1),
            ('transition1', common_features_net[0].transition1)
        ]))
        self.net_2M = nn.Sequential(OrderedDict([
            ('denseblock2', common_features_net[0].denseblock2),
            ('transition2', common_features_net[0].transition2)
        ]))
        self.net_1M = nn.Sequential(OrderedDict([
            ('denseblock3', common_features_net[0].denseblock3),
            ('transition3', common_features_net[0].transition3),
            ('denseblock4', common_features_net[0].denseblock4)
        ]))
    def forward(self, ft_32M):
        
        pretrained_features = [0]*5
        pretrained_features[0] = self.net_16M(ft_32M)
        pretrained_features[1]  = self.net_8M(pretrained_features[0])
        pretrained_features[2]  = self.net_4M(pretrained_features[1])
        pretrained_features[3]  = self.net_2M(pretrained_features[2])
        pretrained_features[4]  = self.net_1M(pretrained_features[3])
        return pretrained_features

if args.debug == True:
#     pass
    print(densenet)
#     common_features_net = nn.Sequential(*list(densenet.children())[0:1])
#     net_x = nn.Sequential(OrderedDict([
#             ('conv0', common_features_net[0].conv0),
#     ]))
    
#     """
#         debug: copy/clone
# #     """
# #     print net_x
#     t = nn.Sequential(*list(net_x.children()))

#     for param in _8M.parameters():
#         print param.data

#     for param in t.parameters():
#         param.data = (param.data*2)
#     print "@@@@@@"

#     for param in t.parameters():
#         print param.data


DenseNet (
  (features): Sequential (
    (conv0): Conv2d(3, 64, kernel_size=(7, 7), stride=(2, 2), padding=(3, 3), bias=False)
    (norm0): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True)
    (relu0): ReLU (inplace)
    (pool0): MaxPool2d (size=(3, 3), stride=(2, 2), padding=(1, 1), dilation=(1, 1))
    (denseblock1): _DenseBlock (
      (denselayer1): _DenseLayer (
        (norm.1): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True)
        (relu.1): ReLU (inplace)
        (conv.1): Conv2d(64, 128, kernel_size=(1, 1), stride=(1, 1), bias=False)
        (norm.2): BatchNorm2d(128, eps=1e-05, momentum=0.1, affine=True)
        (relu.2): ReLU (inplace)
        (conv.2): Conv2d(128, 32, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1), bias=False)
      )
      (denselayer2): _DenseLayer (
        (norm.1): BatchNorm2d(96, eps=1e-05, momentum=0.1, affine=True)
        (relu.1): ReLU (inplace)
        (conv.1): Conv2d(96, 128, kernel_size=(1, 1), stride=(1, 1), bias=False)
      

In [ ]:

class _DenseLayer(nn.Sequential):
    def __init__(self, num_input_features, growth_rate, bn_size, drop_rate):
        super(_DenseLayer, self).__init__()
        self.add_module('norm1', nn.BatchNorm2d(num_input_features)),
        self.add_module('relu1', nn.ReLU(inplace=True)),
        self.add_module('conv1', nn.Conv2d(num_input_features, bn_size *
                        growth_rate, kernel_size=1, stride=1, bias=False)),
        self.add_module('norm2', nn.BatchNorm2d(bn_size * growth_rate)),
        self.add_module('relu2', nn.ReLU(inplace=True)),
        self.add_module('conv2', nn.Conv2d(bn_size * growth_rate, growth_rate,
                        kernel_size=3, stride=1, padding=1, bias=False)),
        self.drop_rate = drop_rate

    def forward(self, x):
        new_features = super(_DenseLayer, self).forward(x)
        if self.drop_rate > 0:
            new_features = F.dropout(new_features, p=self.drop_rate, training=self.training)
        return torch.cat([x, new_features], 1)


class _DenseBlock(nn.Sequential):
    def __init__(self, num_layers, num_input_features, bn_size, growth_rate, drop_rate):
        super(_DenseBlock, self).__init__()
        for i in range(num_layers):
            layer = _DenseLayer(num_input_features + i * growth_rate, growth_rate, bn_size, drop_rate)
            self.add_module('denselayer%d' % (i + 1), layer)

class _MyTransition(nn.Sequential):
    def __init__(self, num_input_features, num_output_features):
        super(_MyTransition, self).__init__()
        self.add_module('norm', nn.BatchNorm2d(num_input_features))
        self.add_module('relu', nn.ReLU(inplace=True))
        self.add_module('conv', nn.Conv2d(num_input_features, num_output_features,
                                          kernel_size=1, stride=1, bias=False))
        self.add_module('pool', nn.AvgPool2d(kernel_size=3, stride=1, padding=1))


    
class GradientNet(nn.Module):
    def build_blocks(self, num_block, num_init_features):
        bn_size = 4
        growth_rate = 32
        drop_rate = 0
        num_features = num_init_features
        features = nn.Sequential()
        for i, num_layers in enumerate(num_block):
            block = _DenseBlock(num_layers=num_layers, num_input_features=num_features,
                                bn_size=bn_size, growth_rate=growth_rate, drop_rate=drop_rate)
            features.add_module('mydenseblock%d' % (i + 1), block)
            num_features = num_features + num_layers * growth_rate
            
            trans = _MyTransition(num_input_features=num_features, num_output_features=num_features // 2)
            features.add_module('mytransition%d' % (i + 1), trans)
            num_features = num_features // 2
#         return features.cuda()
        return features
    
    def __init__(self, pretrained_model):
        super(GradientNet, self).__init__()
        self.block_config = [(3,3,3),(6,6,6),(12,12,12),(16,16,16),(24,24,24)]
        self.num_input_features = [64,64,128,256,1024]
        self.upsample_config = [2,4,8,16,32]
        
        self.pretrained_model = pretrained_model
        
#         self.denseblocks = [nn.Sequential()] * len(self.block_config)
#         for i in range(0, len(self.block_config)):
        i=0; self.denseblock16 = self.build_blocks(self.block_config[i], self.num_input_features[i])
        i=1; self.denseblock08 = self.build_blocks(self.block_config[i], self.num_input_features[i])
        i=2; self.denseblock04 = self.build_blocks(self.block_config[i], self.num_input_features[i])
        i=3; self.denseblock02 = self.build_blocks(self.block_config[i], self.num_input_features[i])
        i=4; self.denseblock01 = self.build_blocks(self.block_config[i], self.num_input_features[i])
        
        if use_gpu: self.denseblock16.cuda()
        if use_gpu: self.denseblock08.cuda()
        if use_gpu: self.denseblock04.cuda()
        if use_gpu: self.denseblock02.cuda()
        if use_gpu: self.denseblock01.cuda()
            
        self.num_upsample_input_features = [92,176,352,480,800]
#         for i in range(0, len(self.block_config)):

#         i=0; self.upsample16 = nn.ConvTranspose2d(in_channels=self.num_upsample_input_features[i], out_channels=3, kernel_size=self.upsample_config[i], stride=2, padding=0, output_padding=0, groups=1, bias=True, dilation=1)
#         i=1; self.upsample08 = nn.ConvTranspose2d(in_channels=self.num_upsample_input_features[i], out_channels=3, kernel_size=self.upsample_config[i], stride=4, padding=0, output_padding=0, groups=1, bias=True, dilation=1)
#         i=2; self.upsample04 = nn.ConvTranspose2d(in_channels=self.num_upsample_input_features[i], out_channels=3, kernel_size=self.upsample_config[i], stride=8, padding=0, output_padding=0, groups=1, bias=True, dilation=1)
#         i=3; self.upsample02 = nn.ConvTranspose2d(in_channels=self.num_upsample_input_features[i], out_channels=3, kernel_size=self.upsample_config[i], stride=16, padding=0, output_padding=0, groups=1, bias=True, dilation=1)
#         i=4; self.upsample01 = nn.ConvTranspose2d(in_channels=self.num_upsample_input_features[i], out_channels=3, kernel_size=self.upsample_config[i], stride=32, padding=0, output_padding=0, groups=1, bias=True, dilation=1)
        
        i=0; self.upsample16 = nn.ConvTranspose2d(in_channels=self.num_upsample_input_features[i], out_channels=3, kernel_size=self.upsample_config[i], stride=2, padding=0, output_padding=0, groups=1, bias=True, dilation=1)
        i=1; self.upsample08 = nn.ConvTranspose2d(in_channels=self.num_upsample_input_features[i], out_channels=3, kernel_size=self.upsample_config[i], stride=4, padding=0, output_padding=0, groups=1, bias=True, dilation=1)
        i=2; self.upsample04 = nn.Sequential(OrderedDict([
            ('norm', nn.BatchNorm2d(self.num_upsample_input_features[i])),
            ('relu', nn.Sigmoid()),
            ('conv04', nn.Conv2d(self.num_upsample_input_features[i], 3, kernel_size=1, stride=1, bias=False))
#             , 
#             ('upsample04', nn.Upsample(scale_factor=8, mode='bilinear'))
        ]))
        i=3; self.upsample02 = nn.Sequential(OrderedDict([
            ('norm', nn.BatchNorm2d(self.num_upsample_input_features[i])),
            ('relu', nn.Sigmoid()),
            ('conv02', nn.Conv2d(self.num_upsample_input_features[i], 3, kernel_size=1, stride=1, bias=False))
#             , 
#             ('upsample02', nn.Upsample(scale_factor=16, mode='bilinear'))
        ]))
        i=4; self.upsample01 = nn.Sequential(OrderedDict([
            ('norm', nn.BatchNorm2d(self.num_upsample_input_features[i])),
            ('relu', nn.Sigmoid()),
            ('conv01', nn.Conv2d(self.num_upsample_input_features[i], 3, kernel_size=1, stride=1, bias=False))
#             , 
#             ('upsample01', nn.Upsample(scale_factor=32, mode='bilinear'))
        ]))
        
        if use_gpu: self.upsample16.cuda()
        if use_gpu: self.upsample08.cuda()
        if use_gpu: self.upsample04.cuda()
        if use_gpu: self.upsample02.cuda()
        if use_gpu: self.upsample01.cuda()
        
#             if platform.system() == 'Linux': 
#                 self.upsamples[i] = self.upsamples[i].cuda()
#             stride = stride * 2
        
        self.merge = nn.Sequential()
        self.merge_in_channels =  (3*len(self.block_config), 64, 32, 16)
        self.merge_out_channels = (                      64, 32, 16,  3)
        for i in range(0, len(self.merge_out_channels)): 
            self.merge.add_module('merge.conv{}'.format(i), 
                                  nn.Conv2d(in_channels=self.merge_in_channels[i], 
                                            out_channels=self.merge_out_channels[i], kernel_size=1))
            self.merge.add_module('merge.relu{}'.format(i), nn.ReLU(inplace=True))
                                    
    def forward(self, ft_input):
        ft_pretrained = self.pretrained_model(ft_input)

#         ft_predict = [b(ft_pretrained[i]) for i, b in enumerate(self.denseblocks)]
#         ft_upsampled = [up(ft_predict[i]) for i, up in enumerate(self.upsamples)]
        
        ft_predict   = [0]*len(ft_pretrained)
        ft_upsampled = [0]*len(ft_pretrained)
        
        i = 0; ft_predict[i] = self.denseblock16(ft_pretrained[i])
        i = 1; ft_predict[i] = self.denseblock08(ft_pretrained[i])
        i = 2; ft_predict[i] = self.denseblock04(ft_pretrained[i])
        i = 3; ft_predict[i] = self.denseblock02(ft_pretrained[i])
        i = 4; ft_predict[i] = self.denseblock01(ft_pretrained[i])
        
        i = 0; ft_upsampled[i] = self.upsample16(ft_predict[i])
        i = 1; ft_upsampled[i] = self.upsample08(ft_predict[i])
        i = 2; ft_upsampled[i] = self.upsample04(ft_predict[i])
        i = 3; ft_upsampled[i] = self.upsample02(ft_predict[i])
        i = 4; ft_upsampled[i] = self.upsample01(ft_predict[i])
        
#         ft_concated = torch.cat(ft_upsampled, 1)
#         ft_merged = self.merge(ft_concated)
        ft_merged = None
        ft_output = ft_upsampled + [ft_merged]
        return ft_output


In [ ]:
# training loop

args.display_curindex = 0
args.base_lr = 1
args.display_interval = 10
args.momentum = 0.9
args.epoches = 200
args.training_thresholds = [5*4,5*3,5*2,5*1,0,5*5]

writer = SummaryWriter()

pretrained = PreTrainedModel(densenet)
if use_gpu: 
    pretrained.cuda()
    
net = GradientNet(pretrained)
if use_gpu: 
    net.cuda()

if use_gpu: 
    mse_losses = [nn.MSELoss().cuda()] * 6
else:
    mse_losses = [nn.MSELoss()] * 6

parameters = filter(lambda p: p.requires_grad, net.parameters())
optimizer = optim.SGD(parameters, lr=args.base_lr, momentum=args.momentum)

def adjust_learning_rate(optimizer, epoch, reset_lr=None):
    """Sets the learning rate to the initial LR decayed by 10 every 30 epochs"""
    for param_group in optimizer.param_groups:
        if reset_lr != None:
            param_group['lr'] = reset_lr
            continue
        lr = param_group['lr'] * (0.1 ** (epoch // 30))
        param_group['lr'] = lr
        print('lr', param_group['lr'])
        

for epoch in range(args.epoches):
    net.train()
    print('epoch: {} [{}]'.format(epoch, datetime.datetime.now().strftime("%Y-%m-%d %H:%M")))
    adjust_learning_rate(optimizer, epoch)
    run_losses = [0] * len(args.training_thresholds)
    run_cnts   = [0.00001] * len(args.training_thresholds)
    if args.training_thresholds.index(epoch) >= 0: 
        adjust_learning_rate(optimizer, epoch, reset_lr=args.base_lr)
    for ind, data in enumerate(train_loader, 0):
        input_img, gt_albedo, gt_shading, test_scene, img_path = data
        if test_scene[0] == 'alley_1':
            print('alley_1 yes')
        input_img = Variable(input_img)
        gt_albedo = Variable(gt_albedo)
        gt_shading = Variable(gt_shading)
        if platform.system() == 'Linux':
            input_img = input_img.cuda()
            gt_albedo = gt_albedo.cuda()
            gt_shading = gt_shading.cuda()
#         run_losses = [0] * len(mse_losses)
#         run_cnts = [0.00001] * len(mse_losses)
        for (i,threshold) in enumerate(args.training_thresholds):
            if epoch >= threshold:
                optimizer.zero_grad()
                ft_predict = net(input_img)
                if i == 5: s = 1
                else: s = (2**(i+1))
                gt = gt_albedo.cpu().data.numpy()
                n,c,h,w = gt.shape
                gt = gt[0,:,:,:]
                gt = gt.transpose((1,2,0))
                gt = cv2.resize(gt, (h//s, w//s))
#                 gt = cv2.resize(gt, (h,w))
                if args.display_curindex % args.display_interval == 0:
                    cv2.imwrite('snapshot/gt-{}-{}.png'.format(epoch, i), gt[:,:,::-1]*255)
                gt = gt.transpose((2,0,1))
                gt = gt[np.newaxis, :]
                gt = Variable(torch.from_numpy(gt))
                if platform.system() == "Linux": gt = gt.cuda()
                loss = mse_losses[i](ft_predict[i], gt)
                loss_data = loss.data.cpu().numpy()
                writer.add_scalar('{}th iters loss'.format(i), loss_data, global_step=args.display_curindex)
                ma_ = ft_predict[i].max().cpu().data.numpy()
                mi_ = ft_predict[i].min().cpu().data.numpy()
                print('mi', mi_, 'ma', ma_)
                writer.add_scalars('{}th predict'.format(i), {'max': ma_, 'min': mi_}, global_step=args.display_curindex)
#                 run_cnts[i] += 1
                run_losses[i] += loss.data.cpu().numpy()[0]
                loss.backward()
                run_cnts[i] += 1
#                 print('i = ', i, '; weig\n', net.upsample01.weight[0,0,0:4,0:4].data.cpu().numpy())
#                 print('i = ', i, '; grad\n', net.upsample01.weight.grad[0,0,0:4,0:4].data.cpu().numpy())
                optimizer.step()
                
                
                if args.display_curindex % args.display_interval == 0:
                    im = ft_predict[i].cpu().data.numpy()[0].transpose((1,2,0)) * 255
                    cv2.imwrite('snapshot/display-{}-{}.png'.format(epoch, i), im[:,:,::-1])
        
        args.display_curindex += 1

    """ every epoch """
          
    
#     loss_output = 'ind: ' + str(args.display_curindex)
    loss_output = ''
    for i,v in enumerate(run_losses):
        writer.add_scalar('{}th epoches'.format(i), run_losses[i]/ run_cnts[i], global_step=epoch)  
        if i == len(run_losses)-1: 
            loss_output += ' merged: %6f' % (run_losses[i] / run_cnts[i])
            continue
        loss_output += ' %2dM: %6f' % ((2**(4-i)), (run_losses[i] / run_cnts[i]))
    print(loss_output)
    # save at every epoch
    if (epoch+1) % 20 == 0:
        torch.save({
            'epoch': epoch,
            'args' : args,
            'state_dict': net.state_dict(),
            'optimizer': optimizer.state_dict()
        }, 'snapshot/snapshot-{}.pth.tar'.format(epoch))
    
    # test 
    net.eval()
    for i, data in enumerate(test_loader, 0):
        input_img, gt_albedo, gt_shading, test_scene, img_path = data
        input_img = Variable(input_img)
        gt_albedo = Variable(gt_albedo)
        gt_shading = Variable(gt_shading)
        if platform.system() == 'Linux':
            input_img = input_img.cuda(args.gpu_num)
        ft_test = net(input_img)
        for k,v in enumerate(ft_test):
            v = v[0].cpu().data.numpy()
            v = v.transpose(1,2,0)
#             print(v.shape, v.min(), v.max())
            cv2.imwrite('snapshot/snapshot-{}-{}.png'.format(epoch, k), v*255)
        break

epoch: 0 [2017-11-13 13:17]
lr 1.0
mi [-0.08176714] ma [ 0.39372033]
mi [-3.82402658] ma [ 65.48097229]
mi [-1421.93286133] ma [ 91.46065521]
mi [ 0.] ma [ 0.]
mi [ 0.] ma [ 0.]
mi [ 0.] ma [ 0.]
mi [ 0.] ma [ 0.]
mi [ 0.] ma [ 0.]
mi [ 0.] ma [ 0.]
mi [ 0.] ma [ 0.]
mi [ 0.] ma [ 0.]
mi [ 0.] ma [ 0.]
mi [ 0.] ma [ 0.]
mi [ 0.] ma [ 0.]
mi [ 0.] ma [ 0.]
mi [ 0.] ma [ 0.]
mi [ 0.] ma [ 0.]
mi [ 0.] ma [ 0.]
mi [ 0.] ma [ 0.]
mi [ 0.] ma [ 0.]
mi [ 0.] ma [ 0.]
mi [ 0.] ma [ 0.]
mi [ 0.] ma [ 0.]
mi [ 0.] ma [ 0.]
mi [ 0.] ma [ 0.]
mi [ 0.] ma [ 0.]
mi [ 0.] ma [ 0.]
mi [ 0.] ma [ 0.]
mi [ 0.] ma [ 0.]
mi [ 0.] ma [ 0.]
mi [ 0.] ma [ 0.]
mi [ 0.] ma [ 0.]
mi [ 0.] ma [ 0.]
mi [ 0.] ma [ 0.]
mi [ 0.] ma [ 0.]
mi [ 0.] ma [ 0.]
mi [ 0.] ma [ 0.]
mi [ 0.] ma [ 0.]
mi [ 0.] ma [ 0.]
mi [ 0.] ma [ 0.]
mi [ 0.] ma [ 0.]
mi [ 0.] ma [ 0.]
mi [ 0.] ma [ 0.]
mi [ 0.] ma [ 0.]
mi [ 0.] ma [ 0.]
mi [ 0.] ma [ 0.]


In [47]:
# net.upsample01.weight.grad[0,0,0:4,0:4].data[0]
for k,v in enumerate(net.parameters()):
    print (k,v)

0 Parameter containing:
(0 ,0 ,.,.) = 
  7.8276e-02  1.4949e-01  1.6611e-01  ...   1.7676e-01  1.6588e-01  1.4101e-01
  1.7546e-01  2.4408e-01  2.5000e-01  ...   2.7452e-01  2.5245e-01  2.2199e-01
  1.2331e-01  1.6441e-01  1.4922e-01  ...   1.6301e-01  1.6191e-01  1.4061e-01
                 ...                   ⋱                   ...                
 -1.0461e-01 -1.2065e-01 -1.1969e-01  ...  -1.1355e-01 -1.1181e-01 -1.1653e-01
 -1.4747e-01 -1.8658e-01 -1.8272e-01  ...  -2.1694e-01 -2.0213e-01 -1.8302e-01
 -2.0729e-01 -2.7118e-01 -2.8157e-01  ...  -2.8711e-01 -2.4883e-01 -2.2605e-01

(0 ,1 ,.,.) = 
  1.6418e-01  2.4814e-01  2.6538e-01  ...   2.7358e-01  2.5693e-01  2.2483e-01
  2.4226e-01  3.2158e-01  3.2346e-01  ...   3.4569e-01  3.1805e-01  2.8128e-01
  1.5825e-01  2.0253e-01  1.8364e-01  ...   1.9484e-01  1.8966e-01  1.6964e-01
                 ...                   ⋱                   ...                
 -1.2547e-01 -1.8073e-01 -1.8958e-01  ...  -1.7603e-01 -1.7623e-01 -1.7415e-

27 Parameter containing:
 7.3114e-02
 6.9825e-04
 4.3339e-02
 8.1157e-02
 6.4349e-02
 4.9110e-02
 1.2833e-01
 3.2071e-02
 2.4337e-08
 8.8820e-02
 7.0764e-02
 1.2412e-01
 1.0103e-06
 1.0947e-01
 1.5999e-04
 1.0748e-08
 5.0669e-02
 1.0227e-09
 9.0128e-02
 3.2262e-02
 2.0526e-02
 4.4360e-02
 3.4514e-02
 8.5815e-09
 1.9185e-06
 2.5854e-02
 6.9632e-02
 5.3968e-02
 4.0639e-02
 2.8990e-02
 4.7068e-02
-1.1910e-01
 1.3061e-06
-1.4836e-01
 7.5916e-02
 3.1452e-03
 4.5161e-02
 8.2029e-03
 4.5105e-02
 3.8510e-02
 7.6850e-03
 6.9706e-08
-1.4031e-01
 1.6807e-02
 3.3927e-02
 2.4907e-03
 3.5082e-02
 5.3326e-02
 5.6905e-02
 6.4741e-02
 5.2809e-02
 1.4212e-01
 5.4281e-04
 3.5095e-02
 1.6932e-02
 1.0809e-01
 2.6622e-02
 1.3299e-01
 5.4097e-02
 1.5326e-02
 4.4123e-02
 7.7206e-02
 5.3127e-02
 8.8101e-02
 1.9121e-02
 1.0231e-01
 9.0113e-02
 6.4405e-02
 1.0749e-01
 1.4217e-01
 1.3511e-01
 1.4448e-01
 9.1681e-02
 1.3488e-01
 9.2789e-02
 1.0733e-01
 8.9989e-02
 1.5215e-01
 1.2660e-01
 1.1030e-01
 1.0661e-01
 1.

82 Parameter containing:
-0.1453
-0.1606
-0.1043
-0.1811
-0.0796
-0.1122
-0.1706
-0.0578
-0.2386
-0.1943
 0.0770
 0.0112
-0.1200
-0.2471
 0.0258
-0.1665
-0.2090
-0.1348
-0.1532
-0.2709
-0.1379
-0.1928
-0.1770
-0.0896
-0.1600
-0.1632
-0.0891
-0.2041
-0.1479
-0.1705
-0.1050
 0.0490
-0.1660
-0.1023
-0.1265
-0.0720
-0.2087
-0.0505
-0.0676
-0.1520
-0.1835
-0.0925
-0.0949
-0.1880
-0.0822
-0.0856
-0.1346
-0.1894
-0.1522
-0.0821
-0.1794
-0.1639
-0.0530
 0.0357
-0.0954
-0.1540
-0.0792
-0.1627
-0.0031
-0.1590
-0.0868
-0.0762
-0.1163
-0.0304
-0.1405
-0.2147
-0.1354
-0.0572
-0.1124
-0.0742
-0.1818
-0.1209
-0.0538
-0.0172
-0.0843
-0.1669
-0.0259
-0.1309
-0.0734
-0.1611
-0.2309
-0.1833
-0.0805
-0.0739
-0.0802
-0.1561
-0.1373
-0.1773
-0.1079
-0.1932
-0.1611
-0.1256
-0.0927
 0.0303
-0.1016
-0.1533
-0.0756
-0.3727
-0.1745
-0.1177
 0.0938
 0.0317
-0.1149
-0.1515
-0.1565
-0.0063
-0.0599
-0.1353
-0.0999
-0.1282
-0.1037
-0.0738
-0.1431
-0.0659
-0.1565
-0.2277
-0.1821
-0.0136
-0.1084
-0.1500
-0.0755
-0.1105

108 Parameter containing:
 1.1643e-01
 8.8996e-02
 1.2044e-01
 7.1452e-02
 1.5648e-01
 9.2253e-02
 1.4378e-01
 1.6277e-01
 8.5520e-02
 6.4777e-02
 4.4161e-02
 1.4092e-01
 1.4545e-01
 1.6050e-01
 8.9871e-02
 1.0519e-01
 1.9817e-01
 9.7623e-02
 1.5268e-01
 6.9434e-02
 1.5228e-01
 7.9350e-02
 1.5807e-01
 1.4844e-01
 1.7807e-01
 1.9362e-01
 9.9560e-02
 9.3675e-02
 1.1523e-01
 4.9471e-06
 9.0531e-02
 8.7469e-02
 1.5966e-01
 1.3220e-01
 8.5825e-02
 9.1157e-02
 1.1506e-01
 1.3152e-01
 1.1725e-01
 9.7379e-02
 1.3277e-01
 4.1203e-02
 1.0523e-01
 7.3647e-02
 1.1300e-01
 9.8935e-02
 5.8614e-02
 9.5471e-02
 1.2505e-01
 9.9851e-02
 1.1443e-01
 7.1557e-02
 1.2831e-01
 6.7241e-02
 1.2001e-01
 1.8946e-01
 4.9743e-02
 7.7964e-02
 5.0636e-02
 5.9631e-02
 9.1601e-02
 5.3887e-02
 1.2792e-01
 1.3301e-01
 5.3759e-02
 8.9751e-02
 1.9591e-04
 1.2772e-01
 1.0121e-01
 1.0962e-01
 1.0933e-01
 1.4619e-01
 6.5639e-02
 1.3219e-01
 1.4414e-01
 1.3044e-01
 1.0127e-01
 1.4515e-01
 1.2963e-01
 4.6441e-02
 9.6665e-02
 1

164 Parameter containing:
( 0 , 0 ,.,.) = 
  3.3189e-02  1.0257e-03  1.4309e-02
  3.0592e-02  7.0093e-03  1.2763e-02
  6.0548e-03 -1.2904e-02  9.0781e-03

( 0 , 1 ,.,.) = 
  5.1192e-02 -2.1878e-02  2.6231e-02
  5.0931e-02  8.7940e-02  5.4886e-02
  7.3917e-02 -4.8069e-02  5.6575e-02

( 0 , 2 ,.,.) = 
 -1.3043e-02 -3.3209e-02 -1.7059e-02
 -1.0427e-03 -1.1133e-02  5.5441e-03
  2.9810e-02  4.6977e-02  3.2838e-02
    ... 

( 0 ,125,.,.) = 
  1.7218e-03  1.1118e-02  1.8031e-02
 -1.3211e-03 -6.3293e-03 -7.5869e-03
 -2.0616e-02 -1.4755e-02 -3.0491e-02

( 0 ,126,.,.) = 
 -1.0410e-02 -2.7359e-02 -2.4807e-02
 -2.0166e-02 -2.7785e-02 -7.7075e-03
 -6.8160e-03 -9.1337e-03 -1.9468e-02

( 0 ,127,.,.) = 
  1.1759e-02  4.2280e-03  4.8706e-02
  1.8059e-02  1.9199e-02  3.0535e-02
  6.8019e-03  2.6358e-02  3.2251e-02
      ⋮  

( 1 , 0 ,.,.) = 
 -1.7185e-02  6.4077e-03  5.2330e-03
 -2.1844e-04  2.9102e-02  7.0390e-03
 -6.4905e-04 -9.2760e-03  4.1150e-03

( 1 , 1 ,.,.) = 
 -2.2237e-02  1.6701e-03 -5.1176e-0

...

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.


Parameter containing:
 0.1614
 0.6797
 0.9521
 0.8736
 0.2761
 0.2084
 0.5149
 0.1727
 0.5724
 0.4066
 0.6793
 0.5462
 0.2807
 0.6328
 0.7960
 0.6704
 0.9605
 0.3276
 0.3978
 0.7451
 0.4570
 0.5888
 0.4058
 0.5815
 0.1484
 0.6899
 0.2178
 0.6596
 0.3523
 0.2201
 0.8836
 0.1788
 0.7305
 0.1265
 0.9408
 0.9966
 0.1543
 0.7465
 0.7066
 0.9995
 0.5469
 0.1354
 0.1915
 0.9456
 0.1229
 0.1095
 0.6661
 0.0408
 0.7963
 0.8583
 0.5492
 0.8509
 0.8798
 0.9763
 0.1211
 0.2714
 0.0172
 0.7948
 0.9231
 0.1961
 0.8891
 0.1847
 0.5135
 0.2621
 0.1486
 0.8847
 0.2599
 0.9804
 0.4095
 0.2991
 0.5047
 0.1457
 0.8126
 0.1355
 0.6234
 0.7877
 0.8384
 0.3404
 0.0948
 0.7751
 0.0771
 0.0267
 0.6711
 0.8852
 0.7650
 0.2330
 0.2216
 0.1219
 0.8266
 0.3831
 0.8584
 0.5859
 0.2905
 0.4517
 0.5633
 0.1077
 0.2719
 0.3908
 0.0582
 0.1161
 0.7910
 0.9180
 0.4597
 0.4769
 0.2293
 0.2578
 0.2792
 0.1448
 0.9233
 0.7662
 0.0005
 0.6805
 0.5228
 0.0370
 0.9485
 0.6849
 0.5451
 0.3362
 0.5854
 0.8288
 0.3486
 0.9335
 0

1442 Parameter containing:
( 0  , 0  ,.,.) = 
 -1.1713e-03

( 0  , 1  ,.,.) = 
  2.7616e-02

( 0  , 2  ,.,.) = 
  2.2153e-02
      ... 

( 0  ,1277,.,.) = 
  3.4579e-03

( 0  ,1278,.,.) = 
 -2.7351e-02

( 0  ,1279,.,.) = 
  2.4901e-02
        ⋮  

( 1  , 0  ,.,.) = 
 -1.6514e-02

( 1  , 1  ,.,.) = 
 -1.9685e-02

( 1  , 2  ,.,.) = 
 -1.3236e-02
      ... 

( 1  ,1277,.,.) = 
  1.3763e-02

( 1  ,1278,.,.) = 
  1.8703e-02

( 1  ,1279,.,.) = 
  2.5451e-02
        ⋮  

( 2  , 0  ,.,.) = 
 -1.8282e-02

( 2  , 1  ,.,.) = 
  1.9347e-02

( 2  , 2  ,.,.) = 
 -2.4543e-02
      ... 

( 2  ,1277,.,.) = 
 -5.3056e-03

( 2  ,1278,.,.) = 
 -6.4146e-03

( 2  ,1279,.,.) = 
 -2.5052e-02
 ...      
        ⋮  

(125 , 0  ,.,.) = 
  3.9488e-03

(125 , 1  ,.,.) = 
  2.0415e-02

(125 , 2  ,.,.) = 
 -1.2961e-02
      ... 

(125 ,1277,.,.) = 
 -2.1199e-02

(125 ,1278,.,.) = 
 -1.0250e-02

(125 ,1279,.,.) = 
  2.3607e-02
        ⋮  

(126 , 0  ,.,.) = 
 -1.5871e-02

(126 , 1  ,.,.) = 
  3.9815e-03

(126 , 2  ,.

1481 Parameter containing:
( 0 , 0 ,.,.) = 
 -2.9057e-02 -5.9870e-03  6.6881e-03
  6.7008e-03  1.9849e-02  2.1230e-02
  2.9135e-04  2.5843e-02  2.1804e-02

( 0 , 1 ,.,.) = 
 -2.4506e-02 -6.6234e-03  1.2345e-02
 -1.8619e-02 -8.6717e-04  3.0281e-03
 -5.5226e-03  4.4411e-06  1.0536e-02

( 0 , 2 ,.,.) = 
  1.9620e-02 -2.4443e-02  2.1292e-02
 -2.3454e-02 -1.2766e-02 -7.4957e-03
  7.1585e-04  3.3384e-04  2.2161e-02
    ... 

( 0 ,125,.,.) = 
  2.3618e-02  3.9130e-03  1.1586e-02
  2.6196e-02  1.4600e-02 -2.5667e-02
 -3.8296e-03 -9.6291e-03 -1.6983e-02

( 0 ,126,.,.) = 
 -2.6814e-02  1.6978e-02 -2.1371e-02
  9.6549e-03 -2.7541e-02 -1.4989e-03
 -2.0487e-02  2.9040e-02  2.8886e-02

( 0 ,127,.,.) = 
  2.7972e-02  8.3932e-03 -2.4009e-02
  2.1925e-03  1.4511e-02 -1.5565e-02
  4.3565e-03  1.7933e-02 -6.7059e-03
      ⋮  

( 1 , 0 ,.,.) = 
  1.9761e-02 -1.2210e-02 -6.3843e-03
  2.4286e-02  8.9590e-03 -1.3149e-02
  1.9235e-02 -2.1161e-02 -5.7613e-03

( 1 , 1 ,.,.) = 
 -1.4359e-02 -3.4075e-03 -1.4399e-

1513 Parameter containing:
(0 ,0 ,.,.) = 
  0.0653

(0 ,1 ,.,.) = 
 -0.0308

(0 ,2 ,.,.) = 
  0.1007

(0 ,3 ,.,.) = 
 -0.2085

(0 ,4 ,.,.) = 
  0.2034

(0 ,5 ,.,.) = 
  0.1883

(0 ,6 ,.,.) = 
  0.0969

(0 ,7 ,.,.) = 
 -0.2539

(0 ,8 ,.,.) = 
  0.0662

(0 ,9 ,.,.) = 
 -0.2531

(0 ,10,.,.) = 
 -0.0652

(0 ,11,.,.) = 
  0.0443

(0 ,12,.,.) = 
  0.2451

(0 ,13,.,.) = 
  0.0983

(0 ,14,.,.) = 
  0.0488

(1 ,0 ,.,.) = 
 -0.0408

(1 ,1 ,.,.) = 
  0.0401

(1 ,2 ,.,.) = 
  0.1437

(1 ,3 ,.,.) = 
  0.1882

(1 ,4 ,.,.) = 
  0.1493

(1 ,5 ,.,.) = 
 -0.1465

(1 ,6 ,.,.) = 
 -0.0682

(1 ,7 ,.,.) = 
 -0.2321

(1 ,8 ,.,.) = 
 -0.1887

(1 ,9 ,.,.) = 
  0.1114

(1 ,10,.,.) = 
  0.0498

(1 ,11,.,.) = 
 -0.0832

(1 ,12,.,.) = 
 -0.2220

(1 ,13,.,.) = 
  0.0569

(1 ,14,.,.) = 
  0.1701

(2 ,0 ,.,.) = 
 -0.1901

(2 ,1 ,.,.) = 
 -0.2269

(2 ,2 ,.,.) = 
 -0.2308

(2 ,3 ,.,.) = 
  0.1961

(2 ,4 ,.,.) = 
  0.0568

(2 ,5 ,.,.) = 
 -0.0805

(2 ,6 ,.,.) = 
 -0.1172

(2 ,7 ,.,.) = 
  0.1389

(2 ,8 ,.,.) = 
 -0.2533

# Visualize Graph

In [161]:
from graphviz import Digraph
import torch
from torch.autograd import Variable


def make_dot(var, params=None):
    """ Produces Graphviz representation of PyTorch autograd graph

    Blue nodes are the Variables that require grad, orange are Tensors
    saved for backward in torch.autograd.Function

    Args:
        var: output Variable
        params: dict of (name, Variable) to add names to node that
            require grad (TODO: make optional)
    """
    if params is not None:
        assert isinstance(params.values()[0], Variable)
        param_map = {id(v): k for k, v in params.items()}

    node_attr = dict(style='filled',
                     shape='box',
                     align='left',
                     fontsize='12',
                     ranksep='0.1',
                     height='0.2')
    dot = Digraph(node_attr=node_attr, graph_attr=dict(size="12,12"))
    seen = set()

    def size_to_str(size):
        return '('+(', ').join(['%d' % v for v in size])+')'

    def add_nodes(var):
        if var not in seen:
            if torch.is_tensor(var):
                dot.node(str(id(var)), size_to_str(var.size()), fillcolor='orange')
            elif hasattr(var, 'variable'):
                u = var.variable
                name = param_map[id(u)] if params is not None else ''
                node_name = '%s\n %s' % (name, size_to_str(u.size()))
                dot.node(str(id(var)), node_name, fillcolor='lightblue')
            else:
                dot.node(str(id(var)), str(type(var).__name__))
            seen.add(var)
            if hasattr(var, 'next_functions'):
                for u in var.next_functions:
                    if u[0] is not None:
                        dot.edge(str(id(u[0])), str(id(var)))
                        add_nodes(u[0])
            if hasattr(var, 'saved_tensors'):
                for t in var.saved_tensors:
                    dot.edge(str(id(t)), str(id(var)))
                    add_nodes(t)
    add_nodes(var.creator)
    return dot

ModuleNotFoundError: No module named 'graphviz'

In [ ]:
make